In [1]:
import pybaseball
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import pandas as pd
import numpy as np
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.model_selection import train_test_split

In [ ]:
def swing_type(outcome_text):
    out_text = outcome_text.lower()
    swing_pattern = [r'field_out', r'single', r'double', r'triple',
                     r'home_run', r'grounded_into_double_play', r'force_out', 
                     r'sac_fly', r'field_error', r'fielders_choice', r'fielders_choice_out',
                     r'double_play', r'triple_play', r'swinging_strike', r'foul'
    ]
    take_pattern = [r'ball', r'walk', r'hit_by_pitch', r'called_strike', r'intent_walk']

    for p in swing_pattern:
        if p in out_text:
            return 1
    for p in take_pattern:
        if p in out_text:
            return 0
    return 0 # Default to take if not found



In [60]:
batter_info = pybaseball.statcast('2025-10-14', '2025-10-15')
batter_info

This is a large query, it may take a moment to complete


 50%|█████     | 1/2 [00:00<00:00,  2.48it/s]c:\Users\yjain\Desktop\Personal Work\moonshot\.venv\Lib\site-packages\pybaseball\datahelpers\postprocessing.py:59: FutureWarning: errors='ignore' is deprecated and will raise in a future version. Use to_datetime without passing `errors` and catch exceptions explicitly instead
  data_copy[column] = data_copy[column].apply(pd.to_datetime, errors='ignore', format=date_format)
100%|██████████| 2/2 [00:00<00:00,  4.30it/s]
c:\Users\yjain\Desktop\Personal Work\moonshot\.venv\Lib\site-packages\pybaseball\statcast.py:85: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  final_data = pd.concat(dataframe_list, axis=0).convert_dtypes(convert_string=False)


pitch_type  game_date  release_speed  release_pos_x  release_pos_z  \
0           FS 2025-10-14           92.5           -2.0           5.13   
1           FS 2025-10-14           92.7           -1.9           5.06   
2           FS 2025-10-14           92.2          -1.98           4.96   
3           CU 2025-10-14           77.7          -1.72           5.23   
4           FS 2025-10-14           92.2          -2.15           5.02   
..         ...        ...            ...            ...            ...   
249         SL 2025-10-14           83.9          -3.66           5.24   
255         FF 2025-10-14           94.4          -3.69           5.18   
261         CU 2025-10-14           76.7           -3.7           5.54   
272         CU 2025-10-14           78.1          -3.59           5.56   
277         CU 2025-10-14           80.7          -3.67           5.48   

             player_name  batter  pitcher     events      description  ...  \
0    Yamamoto, Yoshinobu  683734   808967  strikeout  swinging_strike  ...   
1    Yamamoto, Yoshinobu  683734   808967        NaN             foul  ...   
2    Yamamoto, Yoshinobu  683734   808967        NaN  swinging_strike  ...   
3    Yamamoto, Yoshinobu  683734   808967        NaN    called_strike  ...   
4    Yamamoto, Yoshinobu  592885   808967  field_out    hit_into_play  ...   
..                   ...     ...      ...        ...              ...  ...   
249      Peralta, Freddy  660271   642547  strikeout  swinging_strike  ...   
255      Peralta, Freddy  660271   642547        NaN             ball  ...   
261      Peralta, Freddy  660271   642547        NaN             ball  ...   
272      Peralta, Freddy  660271   642547        NaN    called_strike  ...   
277      Peralta, Freddy  660271   642547        NaN    called_strike  ...   

     batter_days_until_next_game  api_break_z_with_gravity  api_break_x_arm  \
0                           <NA>                      2.93             1.27   
1                           <NA>                      2.77              1.0   
2                           <NA>                      2.79             1.03   
3                           <NA>                      5.17            -1.01   
4                           <NA>                      2.68             0.83   
..                           ...                       ...              ...   
249                         <NA>                      3.05            -0.33   
255                         <NA>                      1.31             0.65   
261                         <NA>                      4.22            -0.57   
272                         <NA>                      4.21            -0.48   
277                         <NA>                      3.51            -0.38   

     api_break_x_batter_in  arm_angle attack_angle attack_direction  \
0                     1.27       <NA>    23.246788        -37.56476   
1                      1.0       <NA>    18.816442       -15.888104   
2                     1.03       <NA>     24.27595       -29.056842   
3                    -1.01       <NA>         <NA>             <NA>   
4                    -0.83       <NA>     4.197969        32.803111   
..                     ...        ...          ...              ...   
249                   0.33       <NA>    29.550436       -28.863768   
255                  -0.65       <NA>         <NA>             <NA>   
261                   0.57       <NA>         <NA>             <NA>   
272                   0.48       <NA>         <NA>             <NA>   
277                   0.38       <NA>         <NA>             <NA>   

    swing_path_tilt intercept_ball_minus_batter_pos_x_inches  \
0         31.768899                                23.619689   
1         39.127436                                31.234674   
2         39.826666                                34.491488   
3              <NA>                                     <NA>   
4         31.639554                                44.53

In [61]:
shortened_data = batter_info[['batter', 'pitch_type', 'description', 'plate_x', 'plate_z', 'events', 'release_speed', 'release_pos_x', 'launch_speed', 'launch_angle', 'effective_speed', 'release_spin_rate', 'release_extension', 'hc_x', 'hc_y']]
pruned_data = shortened_data
print(pruned_data.shape)
pruned_data

(280, 15)


batter pitch_type      description  plate_x  plate_z     events  \
0    683734         FS  swinging_strike    -1.19     2.03  strikeout   
1    683734         FS             foul    -0.58     0.97        NaN   
2    683734         FS  swinging_strike    -0.25     0.81        NaN   
3    683734         CU    called_strike     0.44     1.86        NaN   
4    592885         FS    hit_into_play    -0.51     2.59  field_out   
..      ...        ...              ...      ...      ...        ...   
249  660271         SL  swinging_strike    -0.02      1.3  strikeout   
255  660271         FF             ball     0.95     1.19        NaN   
261  660271         CU             ball    -1.47      1.3        NaN   
272  660271         CU    called_strike     -0.4     3.41        NaN   
277  660271         CU    called_strike     0.11     2.86        NaN   

     release_speed  release_pos_x  launch_speed  launch_angle  \
0             92.5           -2.0          <NA>          <NA>   
1             92.7           -1.9          38.6            30   
2             92.2          -1.98          <NA>          <NA>   
3             77.7          -1.72          <NA>          <NA>   
4             92.2          -2.15          69.5           -59   
..             ...            ...           ...           ...   
249           83.9          -3.66          <NA>          <NA>   
255           94.4          -3.69          <NA>          <NA>   
261           76.7           -3.7          <NA>          <NA>   
272           78.1          -3.59          <NA>          <NA>   
277           80.7          -3.67          <NA>          <NA>   

     effective_speed  release_spin_rate  release_extension    hc_x    hc_y  
0               92.3               1353                6.6    <NA>    <NA>  
1               93.1               1519                6.6    <NA>    <NA>  
2               92.5               1512                6.6    <NA>    <NA>  
3               77.5               2711                6.8    <NA>    <NA>  
4               92.6               1457                6.5  132.17  182.24  
..               ...                ...                ...     ...     ...  
249             84.2               2242                6.6    <NA>    <NA>  
255             94.1               2480                6.6    <NA>    <NA>  
261             76.6               2234                6.3    <NA>    <NA>  
272             77.9               2298                6.2    <NA>    <NA>  
277             80.9               2198                6.5    <NA>    <NA>  

[280 rows x 15 columns]

In [ ]:
both_na = pruned_data['hc_x'].isna() & pruned_data['hc_y'].isna()
both_na_2 = pruned_data['launch_speed'].isna() & pruned_data['launch_angle'].isna()

#pruned_data.loc[both_na_2, 'launch_speed'] = 0
#pruned_data.loc[both_na_2, 'launch_angle'] = 0

pruned_data['outcome_text'] = pruned_data['events']

pruned_data['outcome_text'] = pruned_data['description'].where(both_na, pruned_data['events'])

pruned_data





C:\Users\yjain\AppData\Local\Temp\ipykernel_20432\1958229304.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pruned_data['outcome_text'] = pruned_data['events']
C:\Users\yjain\AppData\Local\Temp\ipykernel_20432\1958229304.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pruned_data['outcome_text'] = pruned_data['description'].where(both_na, pruned_data['events'])


batter pitch_type      description  plate_x  plate_z     events  \
0    683734         FS  swinging_strike    -1.19     2.03  strikeout   
1    683734         FS             foul    -0.58     0.97        NaN   
2    683734         FS  swinging_strike    -0.25     0.81        NaN   
3    683734         CU    called_strike     0.44     1.86        NaN   
4    592885         FS    hit_into_play    -0.51     2.59  field_out   
..      ...        ...              ...      ...      ...        ...   
249  660271         SL  swinging_strike    -0.02      1.3  strikeout   
255  660271         FF             ball     0.95     1.19        NaN   
261  660271         CU             ball    -1.47      1.3        NaN   
272  660271         CU    called_strike     -0.4     3.41        NaN   
277  660271         CU    called_strike     0.11     2.86        NaN   

     release_speed  release_pos_x  launch_speed  launch_angle  \
0             92.5           -2.0           0.0             0   
1             92.7           -1.9          38.6            30   
2             92.2          -1.98           0.0             0   
3             77.7          -1.72           0.0             0   
4             92.2          -2.15          69.5           -59   
..             ...            ...           ...           ...   
249           83.9          -3.66           0.0             0   
255           94.4          -3.69           0.0             0   
261           76.7           -3.7           0.0             0   
272           78.1          -3.59           0.0             0   
277           80.7          -3.67           0.0             0   

     effective_speed  release_spin_rate  release_extension    hc_x    hc_y  \
0               92.3               1353                6.6    <NA>    <NA>   
1               93.1               1519                6.6    <NA>    <NA>   
2               92.5               1512                6.6    <NA>    <NA>   
3               77.5               2711                6.8    <NA>    <NA>   
4               92.6               1457                6.5  132.17  182.24   
..               ...                ...                ...     ...     ...   
249             84.2               2242                6.6    <NA>    <NA>   
255             94.1               2480                6.6    <NA>    <NA>   
261             76.6               2234                6.3    <NA>    <NA>   
272             77.9               2298                6.2    <NA>    <NA>   
277             80.9               2198                6.5    <NA>    <NA>   

        outcome_text  
0    swinging_strike  
1               foul  
2    swinging_strike  
3      called_strike  
4          field_out  
..               ...  
249  swinging_strike  
255             ball  
261             ball  
272    called_strike  
277    called_strike  

[280 rows x 16 columns]

In [ ]:
 # We may not need this as 'batter' is already a label, sike i lied
batter_enc = LabelEncoder() 
pruned_data['batter_id'] = batter_enc.fit_transform(pruned_data['batter'])
pitch_enc = LabelEncoder()
pruned_data['pitch_type_id'] = pitch_enc.fit_transform(pruned_data['pitch_type'])
outcome_enc = LabelEncoder()
pruned_data['outcome_id'] = outcome_enc.fit_transform(pruned_data['outcome_text'])

NUM_BATTERS = pruned_data['batter'].nunique()
NUM_PITCHES = pruned_data['pitch_type_id'].nunique()
NUM_OUTCOMES = pruned_data['outcome_id'].nunique()

scaler = StandardScaler()
pruned_data[['release_speed', 'release_pos_x', 'plate_x', 'plate_z', 'launch_speed', 'launch_angle', 'effective_speed', 'release_spin_rate', 'release_extension']] = scaler.fit_transform(pruned_data[['release_speed', 'release_pos_x', 'plate_x', 'plate_z', 'launch_speed', 'launch_angle', 'effective_speed', 'release_spin_rate', 'release_extension']].astype(float))
pruned_data.head()

print(pruned_data['events'].value_counts())

pruned_data = pruned_data[pruned_data['events'] != 'catcher_interf']

print(pruned_data['outcome_id'].value_counts())
print(pruned_data['events'].values)
labels = set(pruned_data['events'].values)
labels = list(labels)
print(labels)
print(NUM_OUTCOMES)
print(NUM_PITCHES)


events
field_out                    33
single                        7
double                        4
home_run                      3
grounded_into_double_play     2
sac_bunt                      1
force_out                     1
field_error                   1
Name: count, dtype: int64
outcome_id
2    33
7     7
0     4
5     3
4     2
6     1
3     1
1     1
Name: count, dtype: int64
['field_out' 'field_out' 'grounded_into_double_play' 'double' 'field_out'
 'field_out' 'field_out' 'single' 'field_out' 'single' 'field_out'
 'field_out' 'field_out' 'field_out' 'single' 'sac_bunt' 'double'
 'field_out' 'field_out' 'field_out' 'single' 'home_run' 'field_out'
 'field_out' 'field_out' 'field_out' 'grounded_into_double_play' 'single'
 'field_out' 'double' 'field_out' 'field_out' 'field_out' 'single'
 'field_out' 'field_out' 'field_out' 'field_out' 'field_out' 'force_out'
 'field_error' 'field_out' 'double' 'single' 'field_out' 'home_run'
 'field_out' 'field_out' 'field_out' 'field_out' 'ho

C:\Users\yjain\AppData\Local\Temp\ipykernel_20432\192027553.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pruned_data['batter_id'] = batter_enc.fit_transform(pruned_data['batter'])
C:\Users\yjain\AppData\Local\Temp\ipykernel_20432\192027553.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pruned_data['pitch_type_id'] = pitch_enc.fit_transform(pruned_data['pitch_type'])
C:\Users\yjain\AppData\Local\Temp\ipykernel_20432\192027553.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of

In [5]:
class SuperDataSet(Dataset):
    def __init__(self, df):
        self.df = df.reset_index(drop=True)
    def __getitem__(self, index):
        row = self.df.loc[index]
        batter_id = int(row['batter_id'])
        pitch_type_id = int(row['pitch_type_id'])
        features = torch.tensor(row[['release_speed', 'release_pos_x', 'plate_x', 'plate_z', 'launch_speed', 'launch_angle', 'effective_speed', 'release_spin_rate', 'release_extension']].values.astype(np.float32), dtype=torch.float32)
        y = int(row['outcome_id'])
        return batter_id, pitch_type_id, features, y
    def __len__(self):
        return len(self.df)




train_df, test_df = train_test_split(pruned_data, test_size=0.2, random_state=42, stratify=pruned_data['outcome_id'])

train_dataset = SuperDataSet(train_df)
test_dataset = SuperDataSet(test_df)

print(f"Train dataset size: {len(train_dataset)}")
print(train_dataset[1])
print(f"Test dataset size: {len(test_dataset)}")
print(test_dataset[1])

train_loader = DataLoader(train_dataset, batch_size=2, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=2, shuffle=False)



Train dataset size: 9370
(404, 0, tensor([ 0.6164, -0.7102,  0.2110, -2.0017, -0.9331, -0.6823,  0.6349, -1.4158,
         0.2322]), 4)
Test dataset size: 2343
(47, 9, tensor([-2.0610,  1.3770,  1.0002, -1.5800, -0.0182, -0.1238, -1.7991,  0.9626,
         1.2921]), 4)


In [6]:
class SuperModel(nn.Module):
    def __init__(self, num_batters, num_pitch_types, num_input_data_types, output_dim, batter_embedding=10, pitch_embedding=5, hidden_dim=64): #Mess around with batter_embedding, pitch_embedding, hidden_dim
        super().__init__()
        self.batter_embedding = nn.Embedding(num_batters, batter_embedding)
        self.pitch_embedding = nn.Embedding(num_pitch_types, pitch_embedding)
        self.linear1 = nn.Linear(num_input_data_types, 32)
        self.linear2 = nn.Linear(32, 16)

        self.fc1 = nn.Linear(batter_embedding + pitch_embedding + 16, hidden_dim)
        self.relu = nn.ReLU()
        self.fc2 = nn.Linear(hidden_dim, output_dim)
    def forward(self, batter_id, pitch_id, input_data):
        b = self.batter_embedding(batter_id)
        p = self.pitch_embedding(pitch_id) 
        i = self.linear1(input_data)
        i = self.relu(i)
        i = self.linear2(i)
        i = self.relu(i)
        x = torch.cat([b, p, i], dim=1)
        x = self.fc1(x)
        x = self.relu(x)
        x = self.fc2(x)
        return x # {'foul': 0.1, 'single': 0.3, ...}

In [7]:
model_t = SuperModel(num_batters=NUM_BATTERS, num_pitch_types=NUM_PITCHES, num_input_data_types=9, output_dim=NUM_OUTCOMES).to('cuda')
loss = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model_t.parameters(), lr=0.001)
print(model_t)


SuperModel(
  (batter_embedding): Embedding(426, 10)
  (pitch_embedding): Embedding(15, 5)
  (linear1): Linear(in_features=9, out_features=32, bias=True)
  (linear2): Linear(in_features=32, out_features=16, bias=True)
  (fc1): Linear(in_features=31, out_features=64, bias=True)
  (relu): ReLU()
  (fc2): Linear(in_features=64, out_features=14, bias=True)
)


In [8]:
for epoch in range(20):
    model_t.train()
    for i, (batter_id, pitch_type_id, features, y) in enumerate(train_loader):
        batter_id = batter_id.to('cuda').long()
        pitch_type_id = pitch_type_id.to('cuda').long()
        features = features.to('cuda')
        y = y.to('cuda')
        logits = model_t(batter_id, pitch_type_id, features)
        loss_value = loss(logits, y)
        optimizer.zero_grad()
        loss_value.backward()
        optimizer.step()
        print(f"Epoch {epoch+1}, Loss: {loss_value.item()}")



Epoch 1, Loss: 2.8843047618865967
Epoch 1, Loss: 2.5935981273651123
Epoch 1, Loss: 2.5854344367980957
Epoch 1, Loss: 2.773350715637207
Epoch 1, Loss: 2.573418140411377
Epoch 1, Loss: 2.5507335662841797
Epoch 1, Loss: 2.753842353820801
Epoch 1, Loss: 2.84395170211792
Epoch 1, Loss: 2.6743197441101074
Epoch 1, Loss: 2.800753116607666
Epoch 1, Loss: 2.658769369125366
Epoch 1, Loss: 2.863813877105713
Epoch 1, Loss: 2.872668743133545
Epoch 1, Loss: 2.607508659362793
Epoch 1, Loss: 2.7920641899108887
Epoch 1, Loss: 2.8218636512756348
Epoch 1, Loss: 2.614853858947754
Epoch 1, Loss: 2.663957357406616
Epoch 1, Loss: 2.6382861137390137
Epoch 1, Loss: 2.5870769023895264
Epoch 1, Loss: 2.5276641845703125
Epoch 1, Loss: 2.600055694580078
Epoch 1, Loss: 2.3193159103393555
Epoch 1, Loss: 2.3192405700683594
Epoch 1, Loss: 2.5277652740478516
Epoch 1, Loss: 2.583566665649414
Epoch 1, Loss: 2.4593148231506348
Epoch 1, Loss: 2.451633930206299
Epoch 1, Loss: 2.460750102996826
Epoch 1, Loss: 2.3623509407043

In [20]:
model_t.eval()
with torch.inference_mode():
    all = []
    for i, (batter_id, pitch_type_id, features, y) in enumerate(test_loader):
        batter_id = batter_id.to('cuda').long()
        pitch_type_id = pitch_type_id.to('cuda').long()
        features = features.to('cuda')
        y = y.to('cuda')
        logits = model_t(batter_id, pitch_type_id, features)
        #print(logits)
        probs = torch.softmax(logits, dim=1).cpu().numpy()
        #print(probs)

        for batch_idx, probs_row in enumerate(probs):
            pred_dict = {}
            for i in range(len(labels)):
                pred_dict[labels[i]] = float(probs_row[i])
            all.append(pred_dict)
            print(pred_dict)
        loss_value = loss(logits, y)
        #print(f"Test Batch {i+1}, Loss: {loss_value.item()}")
        break

{'field_out': 1.400354573070212e-17, 'home_run': 0.0035097720101475716, 'sac_bunt': 0.0009447408956475556, 'fielders_choice': 0.0007860571495257318, 'field_error': 0.8992156982421875, 'sac_fly': 7.235435987240635e-06, 'fielders_choice_out': 0.004601144231855869, 'force_out': 0.021546386182308197, 'triple': 0.03709806874394417, 'double_play': 3.063405779046846e-11, 'grounded_into_double_play': 5.113600565209708e-08, 'double': 1.0558837715279878e-07, 'single': 0.03229055553674698}
{'field_out': 2.331672486653117e-15, 'home_run': 0.0008809870341792703, 'sac_bunt': 1.7903124671647674e-06, 'fielders_choice': 8.429316267211107e-07, 'field_error': 0.1769246608018875, 'sac_fly': 2.977614256894148e-24, 'fielders_choice_out': 3.367744896923002e-21, 'force_out': 3.1178285553323803e-06, 'triple': 0.0002308775146957487, 'double_play': 1.9689255447937794e-15, 'grounded_into_double_play': 3.2557235181815464e-21, 'double': 1.74057591256771e-11, 'single': 0.8219577074050903}
